In [1]:
from umap import UMAP
import pandas as pd
import numpy as np
import plotly.graph_objs as go
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import cross_val_score, train_test_split
from catboost import CatBoostClassifier as CBC, Pool
from sklearn.tree import DecisionTreeClassifier as DTC
from sklearn import tree
from sklearn.preprocessing import OrdinalEncoder
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.metrics import confusion_matrix, accuracy_score
from sklearn import tree
from dtreeviz.trees import *
import hdbscan

In [2]:
#https://towardsdatascience.com/segmenting-credit-card-customers-with-machine-learning-ed4dbcea009c
x = pd.read_csv('/home/skyolia/JupyterProjects/data/credit_card/CC GENERAL.csv', sep=',')
x

CUST_ID      BALANCE  BALANCE_FREQUENCY  PURCHASES  ONEOFF_PURCHASES  \
0     C10001    40.900749           0.818182      95.40              0.00   
1     C10002  3202.467416           0.909091       0.00              0.00   
2     C10003  2495.148862           1.000000     773.17            773.17   
3     C10004  1666.670542           0.636364    1499.00           1499.00   
4     C10005   817.714335           1.000000      16.00             16.00   
...      ...          ...                ...        ...               ...   
8945  C19186    28.493517           1.000000     291.12              0.00   
8946  C19187    19.183215           1.000000     300.00              0.00   
8947  C19188    23.398673           0.833333     144.40              0.00   
8948  C19189    13.457564           0.833333       0.00              0.00   
8949  C19190   372.708075           0.666667    1093.25           1093.25   

      INSTALLMENTS_PURCHASES  CASH_ADVANCE  PURCHASES_FREQUENCY  \
0                      95.40      0.000000             0.166667   
1                       0.00   6442.945483             0.000000   
2                       0.00      0.000000             1.000000   
3                       0.00    205.788017             0.083333   
4                       0.00      0.000000             0.083333   
...                      ...           ...                  ...   
8945                  291.12      0.000000             1.000000   
8946                  300.00      0.000000             1.000000   
8947                  144.40      0.000000             0.833333   
8948                    0.00     36.558778             0.000000   
8949                    0.00    127.040008             0.666667   

      ONEOFF_PURCHASES_FREQUENCY  PURCHASES_INSTALLMENTS_FREQUENCY  \
0                       0.000000                          0.083333   
1                       0.000000                          0.000000   
2                       1.000000                          0.000000   
3                       0.083333                          0.000000   
4                       0.083333                          0.000000   
...                          ...                               ...   
8945                    0.000000                          0.833333   
8946                    0.000000                          0.833333   
8947                    0.000000                          0.666667   
8948                    0.000000                          0.000000   
8949                    0.666667                          0.000000   

      CASH_ADVANCE_FREQUENCY  CASH_ADVANCE_TRX  PURCHASES_TRX  CREDIT_LIMIT  \
0                   0.000000                 0              2        1000.0   
1                   0.250000                 4              0        7000.0   
2                   0.000000                 0             12        7500.0   
3                   0.083333                 1              1        7500.0   
4                   0.000000                 0              1        1200.0   
...                      ...               ...            ...           ...   
8945                0.000000                 0              6        1000.0   
8946                0.000000                 0              6        1000.0   
8947                0.000000                 0              5        1000.0   
8948                0.166667                 2              0         500.0   
8949                0.333333                 2             23        1200.0   

         PAYMENTS  MINIMUM_PAYMENTS  PRC_FULL_PAYMENT  TENURE  
0      201.802084        139.509787          0.000000      12  
1     4103.032597       1072.340217          0.222222      12  
2      622.066742        627.284787          0.000000      12  
3        0.000000               NaN          0.000000      12  
4      678.334763        244.791237          0.000000      12  
...           ...               ...               ...     ...  
8945   325.594462         48.886365  

In [3]:
x['MINIMUM_PAYMENTS'].fillna((x['MINIMUM_PAYMENTS'].median()), inplace=True)
x['CREDIT_LIMIT'].fillna((x['CREDIT_LIMIT'].median()), inplace=True)

In [4]:
x.isna().sum()

CUST_ID                             0
BALANCE                             0
BALANCE_FREQUENCY                   0
PURCHASES                           0
ONEOFF_PURCHASES                    0
INSTALLMENTS_PURCHASES              0
CASH_ADVANCE                        0
PURCHASES_FREQUENCY                 0
ONEOFF_PURCHASES_FREQUENCY          0
PURCHASES_INSTALLMENTS_FREQUENCY    0
CASH_ADVANCE_FREQUENCY              0
CASH_ADVANCE_TRX                    0
PURCHASES_TRX                       0
CREDIT_LIMIT                        0
PAYMENTS                            0
MINIMUM_PAYMENTS                    0
PRC_FULL_PAYMENT                    0
TENURE                              0
dtype: int64

In [5]:
ids = x['CUST_ID']
x.drop(columns=['CUST_ID'], inplace=True)
x

BALANCE  BALANCE_FREQUENCY  PURCHASES  ONEOFF_PURCHASES  \
0       40.900749           0.818182      95.40              0.00   
1     3202.467416           0.909091       0.00              0.00   
2     2495.148862           1.000000     773.17            773.17   
3     1666.670542           0.636364    1499.00           1499.00   
4      817.714335           1.000000      16.00             16.00   
...           ...                ...        ...               ...   
8945    28.493517           1.000000     291.12              0.00   
8946    19.183215           1.000000     300.00              0.00   
8947    23.398673           0.833333     144.40              0.00   
8948    13.457564           0.833333       0.00              0.00   
8949   372.708075           0.666667    1093.25           1093.25   

      INSTALLMENTS_PURCHASES  CASH_ADVANCE  PURCHASES_FREQUENCY  \
0                      95.40      0.000000             0.166667   
1                       0.00   6442.945483             0.000000   
2                       0.00      0.000000             1.000000   
3                       0.00    205.788017             0.083333   
4                       0.00      0.000000             0.083333   
...                      ...           ...                  ...   
8945                  291.12      0.000000             1.000000   
8946                  300.00      0.000000             1.000000   
8947                  144.40      0.000000             0.833333   
8948                    0.00     36.558778             0.000000   
8949                    0.00    127.040008             0.666667   

      ONEOFF_PURCHASES_FREQUENCY  PURCHASES_INSTALLMENTS_FREQUENCY  \
0                       0.000000                          0.083333   
1                       0.000000                          0.000000   
2                       1.000000                          0.000000   
3                       0.083333                          0.000000   
4                       0.083333                          0.000000   
...                          ...                               ...   
8945                    0.000000                          0.833333   
8946                    0.000000                          0.833333   
8947                    0.000000                          0.666667   
8948                    0.000000                          0.000000   
8949                    0.666667                          0.000000   

      CASH_ADVANCE_FREQUENCY  CASH_ADVANCE_TRX  PURCHASES_TRX  CREDIT_LIMIT  \
0                   0.000000                 0              2        1000.0   
1                   0.250000                 4              0        7000.0   
2                   0.000000                 0             12        7500.0   
3                   0.083333                 1              1        7500.0   
4                   0.000000                 0              1        1200.0   
...                      ...               ...            ...           ...   
8945                0.000000                 0              6        1000.0   
8946                0.000000                 0              6        1000.0   
8947                0.000000                 0              5        1000.0   
8948                0.166667                 2              0         500.0   
8949                0.333333                 2             23        1200.0   

         PAYMENTS  MINIMUM_PAYMENTS  PRC_FULL_PAYMENT  TENURE  
0      201.802084        139.509787          0.000000      12  
1     4103.032597       1072.340217          0.222222      12  
2      622.066742        627.284787          0.000000      12  
3        0.000000        312.343947          0.000000      12  
4      678.334763        244.791237          0.000000      12  
...           ...               ...               ...     ...  
8945   325.594462         48.886365          0.500000       6  
8946   275.861322        312.343947          0.000000       6  
8947    81

In [6]:
fig = go.Figure(data=go.Heatmap(z=x.corr(), x=x.columns, y=x.columns))
fig.show()

In [6]:
scaler = MinMaxScaler(feature_range=(0, 1))
cols = x.columns
x = scaler.fit_transform(x)
x = pd.DataFrame(data=x, columns=cols)
x

BALANCE  BALANCE_FREQUENCY  PURCHASES  ONEOFF_PURCHASES  \
0     0.002148           0.818182   0.001945          0.000000   
1     0.168169           0.909091   0.000000          0.000000   
2     0.131026           1.000000   0.015766          0.018968   
3     0.087521           0.636364   0.030567          0.036775   
4     0.042940           1.000000   0.000326          0.000393   
...        ...                ...        ...               ...   
8945  0.001496           1.000000   0.005936          0.000000   
8946  0.001007           1.000000   0.006118          0.000000   
8947  0.001229           0.833333   0.002945          0.000000   
8948  0.000707           0.833333   0.000000          0.000000   
8949  0.019572           0.666667   0.022293          0.026821   

      INSTALLMENTS_PURCHASES  CASH_ADVANCE  PURCHASES_FREQUENCY  \
0                   0.004240      0.000000             0.166667   
1                   0.000000      0.136685             0.000000   
2                   0.000000      0.000000             1.000000   
3                   0.000000      0.004366             0.083333   
4                   0.000000      0.000000             0.083333   
...                      ...           ...                  ...   
8945                0.012939      0.000000             1.000000   
8946                0.013333      0.000000             1.000000   
8947                0.006418      0.000000             0.833333   
8948                0.000000      0.000776             0.000000   
8949                0.000000      0.002695             0.666667   

      ONEOFF_PURCHASES_FREQUENCY  PURCHASES_INSTALLMENTS_FREQUENCY  \
0                       0.000000                          0.083333   
1                       0.000000                          0.000000   
2                       1.000000                          0.000000   
3                       0.083333                          0.000000   
4                       0.083333                          0.000000   
...                          ...                               ...   
8945                    0.000000                          0.833333   
8946                    0.000000                          0.833333   
8947                    0.000000                          0.666667   
8948                    0.000000                          0.000000   
8949                    0.666667                          0.000000   

      CASH_ADVANCE_FREQUENCY  CASH_ADVANCE_TRX  PURCHASES_TRX  CREDIT_LIMIT  \
0                   0.000000           0.00000       0.005587      0.031720   
1                   0.166667           0.03252       0.000000      0.232053   
2                   0.000000           0.00000       0.033520      0.248748   
3                   0.055555           0.00813       0.002793      0.248748   
4                   0.000000           0.00000       0.002793      0.038397   
...                      ...               ...            ...           ...   
8945                0.000000           0.00000       0.016760      0.031720   
8946                0.000000           0.00000       0.016760      0.031720   
8947                0.000000           0.00000       0.013966      0.031720   
8948                0.111111           0.01626       0.000000      0.015025   
8949                0.222222           0.01626       0.064246      0.038397   

      PAYMENTS  MINIMUM_PAYMENTS  PRC_FULL_PAYMENT  TENURE  
0     0.003979          0.001826          0.000000     1.0  
1     0.080893          0.014034          0.222222     1.0  
2     0.012264          0.008210          0.000000     1.0  
3     0.000000          0.004088          0.000000     1.0  
4     0.013374          0.003204          0.000000     1.0  
...        ...               ...               ...     ...  
8945  0.006419          0.000640          0.500000     0.0  
8946  0.005439          0.004088          0.000000     0.0  
8947  0.001602          0.001078          0.250000     0.0  
8948  0.0

In [7]:
%%time
space = {'cluster_selection_epsilon': 618.0742935473809, 'min_cluster_size': 1526.880706058913, 'min_dist': 0.7975655479100832, 'min_samples': 19.248735056278434, 'n_neighbors': 334.554389667165}
model = UMAP(n_neighbors=int(space['n_neighbors']), min_dist=space['min_dist'], n_components=2, n_epochs=20000, random_state=42)
umap = model.fit_transform(x.values)
fig = go.Figure(data=go.Scatter(x=umap[:,0], y=umap[:,1], mode='markers'))
fig.show()

CPU times: user 33min 37s, sys: 720 ms, total: 33min 38s
Wall time: 33min 35s


In [8]:
hp = [789,  72]
clusterer = hdbscan.HDBSCAN(min_cluster_size=int(space['min_cluster_size']), min_samples=int(space['min_samples']), cluster_selection_epsilon=float(space['cluster_selection_epsilon']))
cluster_labels = clusterer.fit_predict(umap)
clusterer.cluster_persistence_, np.unique(cluster_labels, return_counts=True), metrics.silhouette_score(umap, cluster_labels+1, metric='euclidean')

(array([0.08580797, 0.09502521]),
 (array([-1,  0,  1]), array([3779, 2015, 3156])),
 0.13047889)

In [9]:
fig = go.Figure()
for i in np.unique(cluster_labels):
    idx = np.where(cluster_labels==i)[0]
    fig.add_trace(go.Scatter(x=umap[idx,0], y=umap[idx,1], mode='markers', name='cluster_'+str(i)))
fig.show()

In [93]:
df = pd.read_csv('/home/skyolia/JupyterProjects/data/credit_card/CC GENERAL.csv', sep=',')
df['MINIMUM_PAYMENTS'].fillna((df['MINIMUM_PAYMENTS'].median()), inplace=True)
df['CREDIT_LIMIT'].fillna((df['CREDIT_LIMIT'].median()), inplace=True)
df['Clusters'] = cluster_labels
df.to_csv('/home/skyolia/JupyterProjects/data/credit_card/clustered_data.csv', index=False, sep=',')

In [2]:
df = pd.read_csv('/home/skyolia/JupyterProjects/data/credit_card/clustered_data.csv', sep=',')
df

CUST_ID      BALANCE  BALANCE_FREQUENCY  PURCHASES  ONEOFF_PURCHASES  \
0     C10001    40.900749           0.818182      95.40              0.00   
1     C10002  3202.467416           0.909091       0.00              0.00   
2     C10003  2495.148862           1.000000     773.17            773.17   
3     C10004  1666.670542           0.636364    1499.00           1499.00   
4     C10005   817.714335           1.000000      16.00             16.00   
...      ...          ...                ...        ...               ...   
8945  C19186    28.493517           1.000000     291.12              0.00   
8946  C19187    19.183215           1.000000     300.00              0.00   
8947  C19188    23.398673           0.833333     144.40              0.00   
8948  C19189    13.457564           0.833333       0.00              0.00   
8949  C19190   372.708075           0.666667    1093.25           1093.25   

      INSTALLMENTS_PURCHASES  CASH_ADVANCE  PURCHASES_FREQUENCY  \
0                      95.40      0.000000             0.166667   
1                       0.00   6442.945483             0.000000   
2                       0.00      0.000000             1.000000   
3                       0.00    205.788017             0.083333   
4                       0.00      0.000000             0.083333   
...                      ...           ...                  ...   
8945                  291.12      0.000000             1.000000   
8946                  300.00      0.000000             1.000000   
8947                  144.40      0.000000             0.833333   
8948                    0.00     36.558778             0.000000   
8949                    0.00    127.040008             0.666667   

      ONEOFF_PURCHASES_FREQUENCY  PURCHASES_INSTALLMENTS_FREQUENCY  \
0                       0.000000                          0.083333   
1                       0.000000                          0.000000   
2                       1.000000                          0.000000   
3                       0.083333                          0.000000   
4                       0.083333                          0.000000   
...                          ...                               ...   
8945                    0.000000                          0.833333   
8946                    0.000000                          0.833333   
8947                    0.000000                          0.666667   
8948                    0.000000                          0.000000   
8949                    0.666667                          0.000000   

      CASH_ADVANCE_FREQUENCY  CASH_ADVANCE_TRX  PURCHASES_TRX  CREDIT_LIMIT  \
0                   0.000000                 0              2        1000.0   
1                   0.250000                 4              0        7000.0   
2                   0.000000                 0             12        7500.0   
3                   0.083333                 1              1        7500.0   
4                   0.000000                 0              1        1200.0   
...                      ...               ...            ...           ...   
8945                0.000000                 0              6        1000.0   
8946                0.000000                 0              6        1000.0   
8947                0.000000                 0              5        1000.0   
8948                0.166667                 2              0         500.0   
8949                0.333333                 2             23        1200.0   

         PAYMENTS  MINIMUM_PAYMENTS  PRC_FULL_PAYMENT  TENURE  Clusters  
0      201.802084        139.509787          0.000000      12         1  
1     4103.032597       1072.340217          0.222222      12         0  
2      622.066742        627.284787          0.000000      12         0  
3        0.000000        312.343947          0.000000      12         1  
4      678.334763        244.791237          0.000000      12         0  
...           ...               ...      

In [3]:
df.drop(columns=['CUST_ID'], inplace=True)
df.isna().sum()

BALANCE                             0
BALANCE_FREQUENCY                   0
PURCHASES                           0
ONEOFF_PURCHASES                    0
INSTALLMENTS_PURCHASES              0
CASH_ADVANCE                        0
PURCHASES_FREQUENCY                 0
ONEOFF_PURCHASES_FREQUENCY          0
PURCHASES_INSTALLMENTS_FREQUENCY    0
CASH_ADVANCE_FREQUENCY              0
CASH_ADVANCE_TRX                    0
PURCHASES_TRX                       0
CREDIT_LIMIT                        0
PAYMENTS                            0
MINIMUM_PAYMENTS                    0
PRC_FULL_PAYMENT                    0
TENURE                              0
Clusters                            0
dtype: int64

In [4]:
x, y = df[[i for i in df.columns if i!='Clusters']], df[['Clusters']]
train_x, test_x, train_y, test_y = train_test_split(x, y, test_size = 0.2, random_state = 0)
columns = train_x.columns
#train_x, test_x, train_y, test_y = train_x.values, test_x.values, train_y.values, test_y.values

hp = [7.37855883e-05, 4.99178207e-05, 1.70000000e+01]
hp = [hp[0], hp[1], np.round(hp[2]).astype(int)]
clf = DTC(min_samples_split=hp[0], min_samples_leaf=hp[1], max_features=hp[2], random_state=1)
clf.fit(train_x, train_y)
clf.score(train_x, train_y), clf.score(test_x, test_y)

(1.0, 0.9832402234636871)

In [5]:
pred = clf.predict(test_x)
confusion_matrix(test_y, pred), accuracy_score(test_y, pred)

(array([[ 731,   15],
        [  15, 1029]]), 0.9832402234636871)

In [19]:
#tree.plot_tree(clf, feature_names=train_x.columns, class_names=['cl0', 'cl1'])
viz = dtreeviz(clf, train_x.values, train_y.values.ravel(), target_name='Cluster',feature_names=list(test_x.columns), 
               class_names=["cl0", "cl1"], orientation='LR'  # need class_names for classifier
              )
viz.view() 

/home/skyolia/anaconda3/envs/tensorflow_gpuenv/lib/python3.6/site-packages/matplotlib/font_manager.py:1328: UserWarning:

findfont: Font family ['Arial'] not found. Falling back to DejaVu Sans



In [99]:
from sklearn.inspection import permutation_importance
from sklearn.metrics import fbeta_score, make_scorer


result = permutation_importance(clf, test_x, test_y, n_repeats=10, random_state=42, n_jobs=2, scoring='f1_weighted')
fig = go.Figure()
# Use x instead of y argument for horizontal plot
for i in range(train_x.shape[1]):
    fig.add_trace(go.Box(x=result['importances'][i], name=columns[i]))

fig.show()

In [149]:
train_x.loc[train_x['Age']=='Old']

Age  Gender OwnHome  Married Location  Salary  Children Catalogs  \
513  Old    Male    Rent   Single    Close   32400         1       12   
810  Old  Female     Own   Single    Close   12700         2        6   
37   Old  Female     Own  Married    Close   41600         0       18   
890  Old  Female     Own  Married    Close   62800         0       18   
813  Old  Female    Rent  Married    Close   71800         0       24   
..   ...     ...     ...      ...      ...     ...       ...      ...   
849  Old  Female     Own   Single    Close   32500         0       24   
804  Old  Female     Own  Married    Close   26700         0       24   
723  Old    Male     Own  Married      Far   74500         0       18   
9    Old    Male     Own  Married      Far   80700         0       18   
707  Old    Male     Own   Single    Close   41900         0        6   

     AmountSpent  
513        515.0  
810         65.0  
37         982.0  
890       1403.0  
813       1946.0  
..           ...  
849        883.0  
804       1120.0  
723       1413.0  
9         3034.0  
707        654.0  

[157 rows x 9 columns]

In [95]:
import json
clf.save_model(
    "multiclass_model.json",
    format="json",
    pool=pool  # is required for model with cat_features to obtain applicable model
)

multilclass_model = json.load(open("multiclass_model.json", "r"))
multilclass_model['oblivious_trees'][0]

{'leaf_values': [-0.18494623931505347,
  0.16800000250339509,
  0,
  0,
  -0.13513513714880557,
  0.1736263762136082,
  -0.13913043685581372,
  0.19444444734189245],
 'leaf_weights': [174, 63, 0, 0, 25, 79, 34, 420],
 'splits': [{'border': 7.999999046325684,
   'ctr_target_border_idx': 0,
   'split_index': 4,
   'split_type': 'OnlineCtr'},
  {'border': 47550,
   'float_feature_index': 0,
   'split_index': 1,
   'split_type': 'FloatFeature'},
  {'border': 35700,
   'float_feature_index': 0,
   'split_index': 0,
   'split_type': 'FloatFeature'}]}

In [15]:
from sklearn.datasets import *
iris = load_iris()
iris.target.shape

(150,)

In [9]:
reduced_df = pd.DataFrame(data=umap, columns=['umap_1', 'umap_2'])
reduced_df.to_csv('/home/skyolia/JupyterProjects/data/credit_card/reduced_data.csv', sep=',', index=False)

In [10]:
umap

array([[-12.699457, -39.52393 ],
       [-10.11495 , -49.32107 ],
       [-16.605284, -44.837387],
       ...,
       [-13.514652, -43.212513],
       [-10.655134, -44.738758],
       [-11.635626, -44.467594]], dtype=float32)